# PSDSから取得したデータの解析

In [1]:
require "nyaplot"
require "nyaplot3d"
require "json"
require "daru"
require "statsample"

"if(window['d3'] === undefined ||\n   window['Nyaplot'] === undefined){\n    var path = {\"d3\":\"https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min\",\"downloadable\":\"http://cdn.rawgit.com/domitry/d3-downloadable/master/d3-downloadable\"};\n\n\n\n    var shim = {\"d3\":{\"exports\":\"d3\"},\"downloadable\":{\"exports\":\"downloadable\"}};\n\n    require.config({paths: path, shim:shim});\n\n\nrequire(['d3'], function(d3){window['d3']=d3;console.log('finished loading d3');require(['downloadable'], function(downloadable){window['downloadable']=downloadable;console.log('finished loading downloadable');\n\n\tvar script = d3.select(\"head\")\n\t    .append(\"script\")\n\t    .attr(\"src\", \"http://cdn.rawgit.com/domitry/Nyaplotjs/master/release/nyaplot.js\")\n\t    .attr(\"async\", true);\n\n\tscript[0][0].onload = script[0][0].onreadystatechange = function(){\n\n\n\t    var event = document.createEvent(\"HTMLEvents\");\n\t    event.initEvent(\"load_nyaplot\",false,false);\n\t    win

"if(window['d3'] === undefined ||\n   window['Nyaplot'] === undefined){\n    var path = {\"d3\":\"https://cdnjs.cloudflare.com/ajax/libs/d3/3.5.5/d3.min\",\"downloadable\":\"http://cdn.rawgit.com/domitry/d3-downloadable/master/d3-downloadable\",\"THREE\":\"http://cdnjs.cloudflare.com/ajax/libs/three.js/r66/three.min\",\"Elegans\":\"https://cdn.rawgit.com/domitry/elegans/d81a728f62edaeeb67261516a272438fb39fa80a/release/elegans\"};\n\n\n\n    var shim = {\"d3\":{\"exports\":\"d3\"},\"downloadable\":{\"exports\":\"downloadable\"},\"THREE\":{\"exports\":\"THREE\"},\"Elegans\":{\"exports\":\"Elegans\"}};\n\n    require.config({paths: path, shim:shim});\n\n\nrequire(['d3'], function(d3){window['d3']=d3;console.log('finished loading d3');require(['downloadable'], function(downloadable){window['downloadable']=downloadable;console.log('finished loading downloadable');require(['THREE'], function(THREE){window['THREE']=THREE;console.log('finished loading THREE');require(['Elegans'], function(Eleg

true

In [2]:
# センサー名一覧
sensor_names = {
  "32" => :ambient_temp,
  "96" => :systemboard_temp,
  "160" => :cpu1_temp,
  "224" => :cpu2_temp,
  "288" => :dimm_1a_temp,
  "1824" => :main_12v,
  "1888" => :main_5v,
  "1952" => :main_3_3v,
  "2272" => :cpu1_1_8v,
  "2336" => :cpu2_1_8v,
  "2400" => :fan1_sys,
  "2464" => :fan2_sys,
  "2528" => :fan3_sys,
  "2592" => :fan4_sys,
  "2656" => :fan5_sys,
  "3296" => :total_power
}

{"32"=>:ambient_temp, "96"=>:systemboard_temp, "160"=>:cpu1_temp, "224"=>:cpu2_temp, "288"=>:dimm_1a_temp, "1824"=>:main_12v, "1888"=>:main_5v, "1952"=>:main_3_3v, "2272"=>:cpu1_1_8v, "2336"=>:cpu2_1_8v, "2400"=>:fan1_sys, "2464"=>:fan2_sys, "2528"=>:fan3_sys, "2592"=>:fan4_sys, "2656"=>:fan5_sys, "3296"=>:total_power}

In [3]:
define_method :load_json do |file, value_column|
  response = JSON.load(File.read(file))
  data = response["result"]["data"][0]
  time_idx = data["columns"].index { |i| i["name"] == "time" }
  sensor_no_idx = data["columns"].index { |i| i["name"] == "sensor_no" }
  value_idx = data["columns"].index { |i| i["name"] == value_column }

  h = sensor_names.values.each_with_object({time: []}) {|name, h| h[name] = []}
  data["rows"].chunk_while { |i, j|
    i[time_idx] == j[time_idx]
  }.each do |rows|
    h[:time].push(rows[0][time_idx] / 1000.0 / 3600.0 / 24.0) # days since epoch
    rows.each { |row|
      no = row[sensor_no_idx]
      name = sensor_names[no]
      if name =~ /_temp\z/
        value = row[value_idx].to_f / 1000.0 - 273.15  # millikelvin to celsius
      else
        value = row[value_idx].to_f / 1000.0
      end
      h[name].push(value)
    }
  end
  return Daru::DataFrame.new(h, order: [:time] + sensor_names.values)
end
df = load_json("6358153b-064b-5b11-bfc6-2a45cb0dc42a-30d30m.json", "mean")
# df = load_json("24h.json", "value")

#<Daru::DataFrame:69828083241940 @name = 7aab582d-dc5f-49a3-8fda-380d706a1e9b @size = 1399>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16819.1666 12.4040404 16.3535353       30.0       30.0 15.2626262       12.0       5.13        3.4 1.78969696       1.78 6115.15151 6135.75757 5781.81818     6120.0 6008.48484       92.0 
         1 16819.1875 12.7474226       17.0       30.0       30.0       16.0       12.0       5.13        3.4 1.78989690       1.78 6111.34020 6131.13402 5800.82474     6120.0 6012.37113 92.0412371 
         2 16819.2083 12.4000000 16.8700000       30.0       30.0 15.3400000       12.0       5.13        3.4     1.7899       1.78     6112.8     6140.4     5780.4     6120.0     6009.6       92.0 
         3 16819.2291 12.1648936 16.2872340       30.0       30.0       15.0       12.0       5.13        3.4 1.78978723       1.78 6116.17021 6187.65957 5777.87234     6120.0 6014.04255       92.0 
         4   16819.25 11.5412371       16.0       30.0       30.0       15.0       12.0       5.13        3.4       1.79       1.78 6110.10309 6199.17525 5779.79381     6120.0 6014.84536 92.0412371 
         5 16819.2708 11.1226415 15.2169811       30.0       30.0 14.0849056       12.0       5.13        3.4       1.79       1.78 6117.73584 6160.75471 5780.37735     6120.0 6015.84905 92.0377358 
         6 16819.2916 10.5445544 14.9603960       30.0       30.0 13.7227722       12.0       5.13        3.4       1.79       1.78 6118.81188 6144.95049 5779.00990     6120.0 6015.44554 92.0396039 
         7 16819.3125 10.4108910 14.6435643       30.0       30.0 13.1188118       12.0       5.13        3.4       1.79       1.78 6116.43564 6143.76237 5779.00990     6120.0 6011.88118 92.0792079 
         8 16819.3333 10.3602150 14.8279569       30.0       30.0 13.0215053       12.0       5.13        3.4       1.79       1.78 6116.12903 6131.61290 5781.93548     6120.0 6019.35483       92.0 
         9 16819.3541 10.3857142 14.7523809       30.0       30.0 13.1714285       12.0       5.13        3.4       1.79       1.78 6117.71428 6138.28571     5784.0     6120.0 6012.57142 92.0380952 
        10  16819.375 10.2722772 14.1089108       30.0       30.0       13.0       12.0       5.13        3.4       1.79       1.78 6115.24752 6130.69306 5786.13861     6120.0 6013.06930 92.1188118 
        11 16819.3958 9.85567010       14.0       30.0       30.0       13.0       12.0       5.13        3.4 1.78989690       1.78 6116.28865 6129.89690 5792.16494     6120.0 6013.60824 94.1030927 
        12 16819.4166 9.45192307       14.0       30.0       30.0 12.9230769       12.0       5.13        3.4       1.79       1.78 6115.38461 6133.84615 5786.53846     6120.0 6016.15384 93.8461538 
        13 16819.4375 9.47524752 13.9702970       30.0       30.0 12.3168316       12.0       5.13        3.4       1.79       1.78     6120.0 6127.12871 5775.44554     6120.0 6011.88118 92.0792079 
        14 16819.4583 9.80208333       14.0       30.0       30.0       13.0       12.0       5.13        3.4       1.79       1.78    6116.25     6137.5     5787.5     6120.0    6008.75 92.0833333 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...

In [4]:
df.describe

#<Daru::DataFrame:69828083616920 @name = 51e587d3-5cc7-4a94-8b92-fd22c1b58e11 @size = 5>
           ambient_te  cpu1_1_8v  cpu1_temp  cpu2_1_8v  cpu2_temp dimm_1a_te   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys   main_12v  main_3_3v    main_5v systemboar       time total_powe 
     count       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399       1399 
      mean 15.3589261 1.78768880 31.3422294 1.78000049 31.4005586 18.5233879 6117.95604 6160.02397 5801.17070 6130.46499 6017.66550 11.9997485 3.39999055 5.12999979 19.6141565 16834.1425 92.4850394 
       std 4.09929914 0.00271394 2.29256453 8.02591669 2.17546338 4.04870808 153.474391 166.281673 145.439531 164.193560 143.942131 0.00356193 0.00018374 7.71221375 4.14503991 8.78890019 3.73324316 
       min 5.25247524       1.78       30.0       1.78       30.0       10.0 6083.33333     6120.0     5760.0 6118.73684     6000.0      11.94 3.39538461 5.12971153        9.0 16819.1666       92.0 
       max 30.9864864       1.79 53.6826923 1.78020408 49.0272727 33.2162162     9360.0 9702.16216 8938.37837 9715.13513 9201.08108       12.0        3.4       5.13 34.9864864 16849.1458 175.269230

In [5]:
# 相関行列の計算
cm = Statsample::Bivariate.correlation_matrix(df)
open("correlation_matrix.csv", "w") do |f|
  columns = df.vectors.to_a.map(&:to_s)
  f.puts("," + columns.join(","))
  cm.rows.each_with_index do |row, i|
    f.puts(columns[i] + "," + row.join(","))
  end
end
cm

Matrix[[1.0, 0.653880698399219, 0.6393956632687168, 0.4722281858079927, 0.4982188579136234, 0.6418006547455608, -0.06755196609710462, 0.02561155188807312, -0.001851570251426301, -0.5751160161841985, -0.06988214148706844, 0.041080018897518014, 0.0644625793131015, 0.02671018877357189, 0.06576636293849578, 0.04535210148944731, 0.019536906145186574], [0.653880698399219, 1.0, 0.997090393422622, 0.7551488975217812, 0.7991321392373784, 0.9942507363405299, -0.2271179959240272, 0.03783139700048733, -0.05229923114704562, -0.8797753411448944, -0.1374341528561698, 0.18451947050366885, 0.2101792528943062, 0.1653782255477583, 0.2201811197951771, 0.18827154784601094, 0.09418619064921148], [0.6393956632687168, 0.997090393422622, 1.0, 0.7661770825518088, 0.8072136949779555, 0.996556515834726, -0.22500830143151374, 0.036237438203144914, -0.0883631549829295, -0.8782188850723321, -0.1395895641840254, 0.17817812011249662, 0.20477908024085395, 0.15856600852220198, 0.21389839701314248, 0.18193861584131812, 0

In [6]:
# CPU温度・システムボード温度・環境温度の時間推移をプロット

plot = Nyaplot::Plot.new
plot.add_with_df(df, :line, :time, :cpu1_temp).configure do |d|
  d.title("CPU1")
  d.color("#dd4444")
end
plot.add_with_df(df, :line, :time, :cpu2_temp).configure do |d|
  d.title("CPU2")
  d.color("#ddaa44")
end
plot.add_with_df(df, :line, :time, :systemboard_temp).configure do |d|
  d.title("Systemboard")
  d.color("#44bb44")
end
plot.add_with_df(df, :line, :time, :ambient_temp).configure do |d|
  d.title("Ambient")
end
plot.x_label("Time (days since epoch)")
plot.y_label("Temperature (℃)")
plot.legend(true)
plot.show

#<Nyaplot::Frame:0x007f043cc5ecd8 @properties={:panes=>[#<Nyaplot::Plot:0x007f043c449778 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043c449570 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu1_temp, :title=>"CPU1", :color=>"#dd4444"}, :data=>"7aab582d-dc5f-49a3-8fda-380d706a1e9b"}, @xrange=[16819.166666666668, 16849.145833333332], @yrange=[30.0, 53.68269230769232]>, #<Nyaplot::Diagram:0x007f043c448aa8 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu2_temp, :title=>"CPU2", :color=>"#ddaa44"}, :data=>"7aab582d-dc5f-49a3-8fda-380d706a1e9b"}, @xrange=[16819.166666666668, 16849.145833333332], @yrange=[30.0, 49.0272727272727]>, #<Nyaplot::Diagram:0x007f043c4480d0 @properties={:type=>:line, :options=>{:x=>:time, :y=>:systemboard_temp, :title=>"Systemboard", :color=>"#44bb44"}, :data=>"7aab582d-dc5f-49a3-8fda-380d706a1e9b"}, @xrange=[16819.166666666668, 16849.145833333332], @yrange=[9.0, 34.98648648648651]>, #<Nyaplot::Diagram:0x007f043cc5f6b0 @properties={:type=>:line, :options=>{:x=>:time, :y=>:ambient_temp, :title=>"Ambient"}, :data=>"7aab582d-dc5f-49a3-8fda-380d706a1e9b"}, @xrange=[16819.166666666668, 16849.145833333332], @yrange=[5.252475247524785, 30.986486486486513]>], :options=>{:x_label=>"Time (days since epoch)", :y_label=>"Temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[16819.166666666668, 16849.145833333332], :yrange=>[5.252475247524785, 53.68269230769232]}}>], :data=>{"7aab582d-dc5f-49a3-8fda-380d706a1e9b"=>
#<Daru::DataFrame:69828083241940 @name = 7aab582d-dc5f-49a3-8fda-380d706a1e9b @size = 1399>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16819.1666 12.4040404 16.3535353       30.0       30.0 15.2626262       12.0       5.13        3.4 1.78969696       1.78 6115.15151 6135.75757 5781.81818     6120.0 6008.48484       92.0 
         1 16819.1875 12.7474226       17.0       30.0       30.0       16.0       12.0       5.13        3.4 1.78989690       1.78 6111.34020 6131.13402 5800.82474     6120.0 6012.37113 92.0412371 
         2 16819.2083 12.4000000 16.8700000       30.0       30.0 15.3400000       12.0       5.13        3.4     1.7899       1.78     6112.8     6140.4     5780.4     6120.0     6009.6       92.0 
         3 16819.2291 12.1648936 16.2872340       30.0       30.0       15.0       12.0       5.13        3.4 1.78978723       1.78 6116.17021 6187.65957 5777.87234     6120.0 6014.04255       92.0 
         4   16819.25 11.5412371       16.0       30.0       30.0       15.0       12.0       5.13        3.4       1.79       1.78 6110.10309 6199.17525 5779.79381     6120.0 6014.84536 92.0412371 
         5 16819.2708 11.1226415 15.2169811       30.0       30.0 14.0849056       12.0       5.13        3.4       1.79       1.78 6117.73584 6160.75471 5780.37735     6120.0 6015.84905 92.0377358 
         6 16819.2916 10.5445544 14.9603960       30.0       30.0 13.7227722       12.0       5.13        3.4       1.79       1.78 6118.81188 6144.95049 5779.00990     6120.0 6015.44554 92.0396039 
         7 16819.3125 10.4108910 14.6435643       30.0       30.0 13.1188118       12.0       5.13        3.4       1.79       1.78 6116.43564 6143.76237 5779.00990     6120.0 6011.88118 92.0792079 
         8 16819.3333 10.3602150 14.8279569       30.0       30.0 13.0215053       12.0       5.13        3.4       1.79       1.78 6116.12903 6131.61290 5781.93548     6120.0 6019.35483       92.0 
         9 16819.3541 10.3857142 14.7523809       30.0       30.0 13.1714285       12.0       5.13        3.4       1.79       1.78 6117.71428 6138.28571     5784.0     6120.0 6012.57142 92.0380952 
        10  16819.375 10.2722772 14.1089108       30.0       30.0       13.0       12.0       5.13        3.4       1.79       1.78 6115.24752 6130.69306 5786.13861     6120.0 6013.06930 92.1188118 
        11 16819.3958 9.85567010     

## CPU温度と環境温度の相関を調べる

In [7]:
plot = Nyaplot::Plot.new
plot.add_with_df(df, :scatter, :cpu1_temp, :ambient_temp)
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.show

#<Nyaplot::Frame:0x007f043ca42af8 @properties={:panes=>[#<Nyaplot::Plot:0x007f043ca43598 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043ca433e0 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp}, :data=>"7aab582d-dc5f-49a3-8fda-380d706a1e9b"}, @xrange=[30.0, 53.68269230769232], @yrange=[5.252475247524785, 30.986486486486513]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :zoom=>true, :width=>700, :xrange=>[30.0, 53.68269230769232], :yrange=>[5.252475247524785, 30.986486486486513]}}>], :data=>{"7aab582d-dc5f-49a3-8fda-380d706a1e9b"=>
#<Daru::DataFrame:69828083241940 @name = 7aab582d-dc5f-49a3-8fda-380d706a1e9b @size = 1399>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16819.1666 12.4040404 16.3535353       30.0       30.0 15.2626262       12.0       5.13        3.4 1.78969696       1.78 6115.15151 6135.75757 5781.81818     6120.0 6008.48484       92.0 
         1 16819.1875 12.7474226       17.0       30.0       30.0       16.0       12.0       5.13        3.4 1.78989690       1.78 6111.34020 6131.13402 5800.82474     6120.0 6012.37113 92.0412371 
         2 16819.2083 12.4000000 16.8700000       30.0       30.0 15.3400000       12.0       5.13        3.4     1.7899       1.78     6112.8     6140.4     5780.4     6120.0     6009.6       92.0 
         3 16819.2291 12.1648936 16.2872340       30.0       30.0       15.0       12.0       5.13        3.4 1.78978723       1.78 6116.17021 6187.65957 5777.87234     6120.0 6014.04255       92.0 
         4   16819.25 11.5412371       16.0       30.0       30.0       15.0       12.0       5.13        3.4       1.79       1.78 6110.10309 6199.17525 5779.79381     6120.0 6014.84536 92.0412371 
         5 16819.2708 11.1226415 15.2169811       30.0       30.0 14.0849056       12.0       5.13        3.4       1.79       1.78 6117.73584 6160.75471 5780.37735     6120.0 6015.84905 92.0377358 
         6 16819.2916 10.5445544 14.9603960       30.0       30.0 13.7227722       12.0       5.13        3.4       1.79       1.78 6118.81188 6144.95049 5779.00990     6120.0 6015.44554 92.0396039 
         7 16819.3125 10.4108910 14.6435643       30.0       30.0 13.1188118       12.0       5.13        3.4       1.79       1.78 6116.43564 6143.76237 5779.00990     6120.0 6011.88118 92.0792079 
         8 16819.3333 10.3602150 14.8279569       30.0       30.0 13.0215053       12.0       5.13        3.4       1.79       1.78 6116.12903 6131.61290 5781.93548     6120.0 6019.35483       92.0 
         9 16819.3541 10.3857142 14.7523809       30.0       30.0 13.1714285       12.0       5.13        3.4       1.79       1.78 6117.71428 6138.28571     5784.0     6120.0 6012.57142 92.0380952 
        10  16819.375 10.2722772 14.1089108       30.0       30.0       13.0       12.0       5.13        3.4       1.79       1.78 6115.24752 6130.69306 5786.13861     6120.0 6013.06930 92.1188118 
        11 16819.3958 9.85567010       14.0       30.0       30.0       13.0       12.0       5.13        3.4 1.78989690       1.78 6116.28865 6129.89690 5792.16494     6120.0 6013.60824 94.1030927 
        12 16819.4166 9.45192307       14.0       30.0       30.0 12.9230769       12.0       5.13        3.4       1.79       1.78 6115.38461 6133.84615 5786.53846     6120.0 6016.15384 93.8461538 
        13 16819.4375 9.47524752 13.9702970       30.0       30.0 12.3168316       12.0       5.13        3.4       1.79       1.78     6120.0 6127.12871 5775.44554     6120.0 6011.88118 92.0792079 
        14 16819.4583 9.80208333       14.0       30.0       30.0       13.0       12.0       5.13        3.4       1.79       1.78    6116.25     6137.5     5787.5     6120.0    6008.75 92.0833333 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...       

In [8]:
# CPU温度の下限値を除外
filtered_df = df.where(df[:cpu1_temp].gt(30.0))
plot = Nyaplot::Plot.new
plot.add_with_df(filtered_df, :scatter, :cpu1_temp, :ambient_temp)
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.show

#<Nyaplot::Frame:0x007f043c87e910 @properties={:panes=>[#<Nyaplot::Plot:0x007f043c87f3d8 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043c87f220 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp}, :data=>"92364cf0-f141-4a2c-bd66-8cae3dc204ec"}, @xrange=[30.008928571428612, 53.68269230769232], @yrange=[13.17105263157896, 30.986486486486513]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :zoom=>true, :width=>700, :xrange=>[30.008928571428612, 53.68269230769232], :yrange=>[13.17105263157896, 30.986486486486513]}}>], :data=>{"92364cf0-f141-4a2c-bd66-8cae3dc204ec"=>
#<Daru::DataFrame:69828086070360 @name = 92364cf0-f141-4a2c-bd66-8cae3dc204ec @size = 685>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
        43 16820.0625 15.3724489 19.9387755 30.0102040 30.0102040 18.5714285       12.0       5.13        3.4 1.78867346       1.78 6107.75510 6126.12244 5785.71428     6120.0 6002.44897 92.0816326 
        51 16820.2291 15.9950000 20.1500000 30.0100000 30.1100000       19.0       12.0       5.13        3.4      1.789       1.78     6109.2     6130.8     5775.6     6120.0     6008.4       92.0 
        52   16820.25       16.0 20.2666666 30.0285714 30.2190476       19.0       12.0       5.13        3.4 1.78866666       1.78 6113.14285 6126.85714 5774.85714     6120.0 6009.14285 92.0380952 
        53 16820.2708 15.9182692 20.5096153 30.0096153 30.2115384       19.0       12.0       5.13        3.4    1.78875       1.78 6107.30769 6124.61538 5777.30769     6120.0 6006.92307 92.0769230 
       378 16827.0416 15.7475247 19.8514851 30.0099009 30.2277227 18.7821782       12.0       5.13        3.4 1.78841584       1.78 6108.11881 6134.25742 5780.19801     6120.0 6005.94059 92.0396039 
       379 16827.0625 16.3490566 20.7358490 30.1132075 30.8490566 19.5188679       12.0       5.13        3.4 1.78764150       1.78 6103.01886 6131.32075 5782.64150     6120.0 6005.66037 92.0377358 
       380 16827.0833 16.9105263 21.1473684 30.3894736 31.4315789       20.0       12.0       5.13        3.4 1.78778947       1.78 6112.42105     6144.0 5775.15789     6120.0 6002.52631 92.1684210 
       381 16827.1041 17.4770642 21.9541284 31.1376146 31.8348623 20.7339449       12.0       5.13        3.4 1.78706422       1.78 6102.38532 6148.62385 5793.02752     6120.0 6007.70642 92.1100917 
       382  16827.125 17.8457943       22.0 31.5607476 32.1495327       21.0       12.0       5.13        3.4 1.78691588       1.78 6107.66355 6140.18691 5784.67289     6120.0 6004.48598 92.0373831 
       383 16827.1458       18.0 22.2395833 31.6354166 32.3854166       21.0       12.0       5.13        3.4 1.78572916       1.78    6108.75    6136.25     5797.5     6120.0    6001.25       92.0 
       384 16827.1666 18.0098039 22.0882352 31.4313725 32.3039215       21.0       12.0       5.13        3.4 1.78598039       1.78 6101.17647 6129.41176 5790.58823     6120.0 6002.35294 92.0392156 
       385 16827.1875       18.0 22.0761904 31.8761904 32.2952380       21.0       12.0       5.13        3.4 1.78561904       1.78 6109.71428 6133.71428 5793.14285     6120.0 6005.71428 92.0761904 
       386 16827.2083 18.0048076 22.4615384 32.1538461 32.4326923       21.0       12.0       5.13        3.4 1.78528846       1.78 6099.23076 6133.84615 5785.38461     6120.0 6002.30769 92.2692307 
       387 16827.2291 18.2252252 22.9369369 32.1531531 32.6756756       21.0       12.0       5.13        3.4 1.78513513       1.78 6105.94594 6131.89189 5785.94594     6120.0 6005.40540 92.1081081 
       388   16827.25 18.4565217       23.0 32.5652173 32.7173913 21.8152173       12.0       5.13        3.4 1.78434782       1.78 6109.56521 6127.82608 5774.34782     6120.0 6005.21739 92.0434782 
       ...        ...        ...        ...        ...        ...        ...        ...  

In [9]:
# 単回帰分析
sr = Statsample::Regression.simple(filtered_df[:cpu1_temp], filtered_df[:ambient_temp])
cpu1_temp_min = filtered_df[:cpu1_temp].min
cpu1_temp_max = filtered_df[:cpu1_temp].max
df2 = Daru::DataFrame.new(
  cpu1_temp_min.step(cpu1_temp_max, (cpu1_temp_max - cpu1_temp_min) / 10.0).map { |x|
    { x: x, y: sr.a + sr.b * x }
  }
)
plot = Nyaplot::Plot.new
plot.add_with_df(filtered_df, :scatter, :cpu1_temp, :ambient_temp).configure do |d|
  d.title("Sample")
end
plot.add_with_df(df2, :line, :x, :y).configure do |d|
  d.color("#44bb44")
  d.title(format("%.3f + %.3fx", sr.a, sr.b))
end
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.legend(true)
plot.show


#<Nyaplot::Frame:0x007f043cac1a60 @properties={:panes=>[#<Nyaplot::Plot:0x007f043cac3068 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043cac2eb0 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp, :title=>"Sample"}, :data=>"92364cf0-f141-4a2c-bd66-8cae3dc204ec"}, @xrange=[30.008928571428612, 53.68269230769232], @yrange=[13.17105263157896, 30.986486486486513]>, #<Nyaplot::Diagram:0x007f043cac2550 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :color=>"#44bb44", :title=>"1.545 + 0.527x"}, :data=>"8c2e2fa6-da85-42f1-b3b9-4ecfc78131eb"}, @xrange=[30.008928571428612, 53.68269230769232], @yrange=[17.355033011987935, 29.827567011209002]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[30.008928571428612, 53.68269230769232], :yrange=>[13.17105263157896, 30.986486486486513]}}>], :data=>{"92364cf0-f141-4a2c-bd66-8cae3dc204ec"=>
#<Daru::DataFrame:69828086070360 @name = 92364cf0-f141-4a2c-bd66-8cae3dc204ec @size = 685>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
        43 16820.0625 15.3724489 19.9387755 30.0102040 30.0102040 18.5714285       12.0       5.13        3.4 1.78867346       1.78 6107.75510 6126.12244 5785.71428     6120.0 6002.44897 92.0816326 
        51 16820.2291 15.9950000 20.1500000 30.0100000 30.1100000       19.0       12.0       5.13        3.4      1.789       1.78     6109.2     6130.8     5775.6     6120.0     6008.4       92.0 
        52   16820.25       16.0 20.2666666 30.0285714 30.2190476       19.0       12.0       5.13        3.4 1.78866666       1.78 6113.14285 6126.85714 5774.85714     6120.0 6009.14285 92.0380952 
        53 16820.2708 15.9182692 20.5096153 30.0096153 30.2115384       19.0       12.0       5.13        3.4    1.78875       1.78 6107.30769 6124.61538 5777.30769     6120.0 6006.92307 92.0769230 
       378 16827.0416 15.7475247 19.8514851 30.0099009 30.2277227 18.7821782       12.0       5.13        3.4 1.78841584       1.78 6108.11881 6134.25742 5780.19801     6120.0 6005.94059 92.0396039 
       379 16827.0625 16.3490566 20.7358490 30.1132075 30.8490566 19.5188679       12.0       5.13        3.4 1.78764150       1.78 6103.01886 6131.32075 5782.64150     6120.0 6005.66037 92.0377358 
       380 16827.0833 16.9105263 21.1473684 30.3894736 31.4315789       20.0       12.0       5.13        3.4 1.78778947       1.78 6112.42105     6144.0 5775.15789     6120.0 6002.52631 92.1684210 
       381 16827.1041 17.4770642 21.9541284 31.1376146 31.8348623 20.7339449       12.0       5.13        3.4 1.78706422       1.78 6102.38532 6148.62385 5793.02752     6120.0 6007.70642 92.1100917 
       382  16827.125 17.8457943       22.0 31.5607476 32.1495327       21.0       12.0       5.13        3.4 1.78691588       1.78 6107.66355 6140.18691 5784.67289     6120.0 6004.48598 92.0373831 
       383 16827.1458       18.0 22.2395833 31.6354166 32.3854166       21.0       12.0       5.13        3.4 1.78572916       1.78    6108.75    6136.25     5797.5     6120.0    6001.25       92.0 
       384 16827.1666 18.0098039 22.0882352 31.4313725 32.3039215       21.0       12.0       5.13        3.4 1.78598039       1.78 6101.17647 6129.41176 5790.58823     6120.0 6002.35294 92.0392156 
       385 16827.1875       18.0 22.0761904 31.8761904 32.2952380       21.0       12.0       5.13        3.4 1.78561904       1.78 6109.71428 6133.71428 5793.14285     6120.0 6005.71428 92.0761904 
       386 16827.2083 18.0048076 22.4615384 32.1538461 32.4326923       21.0       12.0       5.13        3.4 1.78528846       1.78 6099.23076 6133.84615 5785.38461     6120.0 6002.30769 92.2692307 
       387 16827.2291 18.2252252 22.9369369 32.1531531 32.6756756       21.0       12.0       5.13        3.4 1.78513513       1.78 6105.94594 6131.89189 5785.94594     6

In [10]:
filtered_df.where(filtered_df[:cpu1_temp].gt(31.0) & filtered_df[:ambient_temp].lt(16))

#<Daru::DataFrame:69828066666380 @name = 2e7f43b9-c8d4-4265-bff4-24f58ab351b0 @size = 1>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
      1257 16846.2083 15.5263157 21.1578947      31.75 31.9342105 20.0131578       12.0       5.13        3.4 1.78631578       1.78 6102.63157 6162.63157 5775.78947     6120.0 6011.05263 92.1052631

In [11]:
# マハラノビス距離の計算

covariance_matrix = Statsample::Bivariate.covariance_matrix(Daru::DataFrame.new(cpu1_temp: filtered_df[:cpu1_temp],
                                                                                ambient_temp: filtered_df[:ambient_temp]))
vi = covariance_matrix.inverse
delta = (filtered_df[:cpu1_temp] - filtered_df[:cpu1_temp].mean).zip(filtered_df[:ambient_temp] - filtered_df[:ambient_temp].mean)
mhalanobis_distance = delta.map { |a|
  v = Vector[*a]
  Math.sqrt((v.transpose * vi * v)[0])
}
df3 = Daru::DataFrame.new(time: filtered_df[:time], cpu1_temp: filtered_df[:cpu1_temp], ambient_temp: filtered_df[:ambient_temp],
  mhalanobis_distance: mhalanobis_distance)
df3.plot type: :line, x: :time, y: :mhalanobis_distance

#<Nyaplot::Frame:0x007f043c06f918 @properties={:panes=>[#<Nyaplot::Plot:0x007f043cfae4b0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043c06ff08 @properties={:type=>:line, :options=>{:x=>:time, :y=>:mhalanobis_distance}, :data=>"ba3a8bb6-96ab-4b21-ab86-33416d887fa7"}, @xrange=[16820.0625, 16849.145833333332], @yrange=[0.04591340183893721, 17.967267356298034]>], :options=>{:zoom=>true, :width=>700, :xrange=>[16820.0625, 16849.145833333332], :yrange=>[0.04591340183893721, 17.967267356298034]}}>], :data=>{"ba3a8bb6-96ab-4b21-ab86-33416d887fa7"=>#<Nyaplot::DataFrame:0x007f043c43cbb8 @name="ba3a8bb6-96ab-4b21-ab86-33416d887fa7", @rows=[{:ambient_temp=>15.372448979591866, :cpu1_temp=>30.010204081632708, :mhalanobis_distance=>1.3157150721076427, :time=>16820.0625}, {:ambient_temp=>15.995000000000005, :cpu1_temp=>30.010000000000048, :mhalanobis_distance=>1.2122441243613995, :time=>16820.229166666668}, {:ambient_temp=>16.0, :cpu1_temp=>30.028571428571468, :mhalanobis_distance=>1.2045226089361623, :time=>16820.25}, {:ambient_temp=>15.918269230769283, :cpu1_temp=>30.009615384615415, :mhalanobis_distance=>1.2163065014700156, :time=>16820.270833333332}, {:ambient_temp=>15.747524752475272, :cpu1_temp=>30.009900990099027, :mhalanobis_distance=>1.234193319869579, :time=>16827.041666666668}, {:ambient_temp=>16.349056603773647, :cpu1_temp=>30.11320754716985, :mhalanobis_distance=>1.1723268595451282, :time=>16827.0625}, {:ambient_temp=>16.910526315789525, :cpu1_temp=>30.389473684210543, :mhalanobis_distance=>1.0966762233309235, :time=>16827.083333333332}, {:ambient_temp=>17.47706422018348, :cpu1_temp=>31.13761467889907, :mhalanobis_distance=>0.7406783417171264, :time=>16827.104166666668}, {:ambient_temp=>17.845794392523374, :cpu1_temp=>31.560747663551467, :mhalanobis_distance=>0.5498062218460752, :time=>16827.125}, {:ambient_temp=>18.0, :cpu1_temp=>31.635416666666686, :mhalanobis_distance=>0.5403294268259872, :time=>16827.145833333332}, {:ambient_temp=>18.00980392156862, :cpu1_temp=>31.431372549019613, :mhalanobis_distance=>0.6963455668338857, :time=>16827.166666666668}, {:ambient_temp=>18.0, :cpu1_temp=>31.876190476190516, :mhalanobis_distance=>0.3868200144359917, :time=>16827.1875}, {:ambient_temp=>18.004807692307736, :cpu1_temp=>32.15384615384613, :mhalanobis_distance=>0.3006869286846082, :time=>16827.208333333332}, {:ambient_temp=>18.225225225225245, :cpu1_temp=>32.15315315315314, :mhalanobis_distance=>0.2610618103220469, :time=>16827.229166666668}, {:ambient_temp=>18.456521739130437, :cpu1_temp=>32.56521739130437, :mhalanobis_distance=>0.14290395701640002, :time=>16827.25}, {:ambient_temp=>18.49509803921569, :cpu1_temp=>32.43137254901961, :mhalanobis_distance=>0.13758427749626267, :time=>16827.270833333332}, {:ambient_temp=>18.418269230769283, :cpu1_temp=>32.49038461538464, :mhalanobis_distance=>0.1449320845381872, :time=>16827.291666666668}, {:ambient_temp=>18.046391752577335, :cpu1_temp=>32.13402061855675, :mhalanobis_distance=>0.2890114818791632, :time=>16827.3125}, {:ambient_temp=>17.941860465116292, :cpu1_temp=>32.32558139534882, :mhalanobis_distance=>0.37171584360617, :time=>16827.333333333332}, {:ambient_temp=>17.509433962264154, :cpu1_temp=>31.735849056603797, :mhalanobis_distance=>0.4919654225101283, :time=>16827.354166666668}, {:ambient_temp=>17.46296296296299, :cpu1_temp=>31.472222222222285, :mhalanobis_distance=>0.5647588353786142, :time=>16827.375}, {:ambient_temp=>17.071428571428612, :cpu1_temp=>31.132653061224516, :mhalanobis_distance=>0.7185767288909698, :time=>16827.395833333332}, {:ambient_temp=>16.367647058823593, :cpu1_temp=>30.803921568627516, :mhalanobis_distance=>0.9331505829358071, :time=>16827.416666666668}, {:ambient_temp=>16.029702970297024, :cpu1_temp=>30.059405940594047, :mhalanobis_distance=>1.190915230143838, :time=>16827.4375}, {:ambient_temp=>15.322916666666686, :cpu1_temp=>30.020833333333314, :mhalanobis_distance=>1.3293910737922645, :time=>16827.458333333332}, {:ambient_temp=>16.386363636363683, :cpu1

In [12]:
# マハラノビス距離が4より大きいデータを表示
df3.where(df3[:mhalanobis_distance].gt(4))

#<Daru::DataFrame:69828067762360 @name = a6bde7ba-eb58-4013-81c7-d37b83ceda0b @size = 8>
           ambient_te  cpu1_temp mhalanobis       time 
       180 18.7980769 53.6826923 17.9672673 16832.4583 
       181 19.1603773 49.7924528 14.4012679 16832.4791 
       182 21.0818181 53.5636363 16.4476875    16832.5 
       429 28.7905405 42.2432432 4.23024310 16843.1458 
       430 29.9324324 43.1081081 4.63390237 16843.1666 
       431 30.9864864 44.3648648 5.17244749 16843.1875 
       432 30.2800000 43.5866666 4.83374172 16843.2083 
       679 21.7183098 41.3239436 5.63154713 16849.0416

In [13]:
# マハラノビス距離が4より小さいデータのみで単回帰分析
df4 = df3.where(df3[:mhalanobis_distance].lt(4))
sr = Statsample::Regression.simple(df4[:cpu1_temp], df4[:ambient_temp])
cpu1_temp_min = df4[:cpu1_temp].min
cpu1_temp_max = df4[:cpu1_temp].max
df5 = Daru::DataFrame.new(
  cpu1_temp_min.step(cpu1_temp_max, (cpu1_temp_max - cpu1_temp_min) / 10.0).map { |x|
    { x: x, y: sr.a + sr.b * x }
  }
)
plot = Nyaplot::Plot.new
plot.add_with_df(df4, :scatter, :cpu1_temp, :ambient_temp).configure do |d|
  d.title("Sample")
end
plot.add_with_df(df5, :line, :x, :y).configure do |d|
  d.color("#44bb44")
  d.title(format("%.3f + %.3fx", sr.a, sr.b))
end
plot.x_label("CPU1 temperature (℃)")
plot.y_label("Ambient temperature (℃)")
plot.legend(true)
plot.show

#<Nyaplot::Frame:0x007f043a148580 @properties={:panes=>[#<Nyaplot::Plot:0x007f043a14a6a0 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043a14a4e8 @properties={:type=>:scatter, :options=>{:x=>:cpu1_temp, :y=>:ambient_temp, :title=>"Sample"}, :data=>"ea254c6c-ec4f-4c84-9079-508b36e68506"}, @xrange=[30.008928571428612, 41.66216216216219], @yrange=[13.17105263157896, 27.554794520548]>, #<Nyaplot::Diagram:0x007f043a149840 @properties={:type=>:line, :options=>{:x=>:x, :y=>:y, :color=>"#44bb44", :title=>"-12.489 + 0.958x"}, :data=>"735de913-3d6f-4a17-bcd3-14b0396227ad"}, @xrange=[30.008928571428612, 41.66216216216219], @yrange=[16.2579358799218, 27.421248951870854]>], :options=>{:x_label=>"CPU1 temperature (℃)", :y_label=>"Ambient temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[30.008928571428612, 41.66216216216219], :yrange=>[13.17105263157896, 27.554794520548]}}>], :data=>{"ea254c6c-ec4f-4c84-9079-508b36e68506"=>
#<Daru::DataFrame:69828066405600 @name = ea254c6c-ec4f-4c84-9079-508b36e68506 @size = 677>
           ambient_te  cpu1_temp mhalanobis       time 
         0 15.3724489 30.0102040 1.31571507 16820.0625 
         1 15.9950000 30.0100000 1.21224412 16820.2291 
         2       16.0 30.0285714 1.20452260   16820.25 
         3 15.9182692 30.0096153 1.21630650 16820.2708 
         4 15.7475247 30.0099009 1.23419331 16827.0416 
         5 16.3490566 30.1132075 1.17232685 16827.0625 
         6 16.9105263 30.3894736 1.09667622 16827.0833 
         7 17.4770642 31.1376146 0.74067834 16827.1041 
         8 17.8457943 31.5607476 0.54980622  16827.125 
         9       18.0 31.6354166 0.54032942 16827.1458 
        10 18.0098039 31.4313725 0.69634556 16827.1666 
        11       18.0 31.8761904 0.38682001 16827.1875 
        12 18.0048076 32.1538461 0.30068692 16827.2083 
        13 18.2252252 32.1531531 0.26106181 16827.2291 
        14 18.4565217 32.5652173 0.14290395   16827.25 
       ...        ...        ...        ...        ... 
, "735de913-3d6f-4a17-bcd3-14b0396227ad"=>
#<Daru::DataFrame:69828065535620 @name = 735de913-3d6f-4a17-bcd3-14b0396227ad @size = 11>
                    x          y 
         0 30.0089285 16.2579358 
         1 31.1742519 17.3742671 
         2 32.3395752 18.4905984 
         3 33.5048986 19.6069298 
         4 34.6702220 20.7232611 
         5 35.8355453 21.8395924 
         6 37.0008687 22.9559237 
         7 38.1661920 24.0722550 
         8 39.3315154 25.1885863 
         9 40.4968388 26.3049176 
        10 41.6621621 27.4212489 
}, :extension=>["Elegans"]}>

In [14]:
plot = Nyaplot::Plot.new
plot.add_with_df(df, :line, :time, :cpu1_1_8v)
plot.x_label("Time (days since epoch)")
plot.y_label("CPU1 Voltage (W)")
plot.show

#<Nyaplot::Frame:0x007f043ce36948 @properties={:panes=>[#<Nyaplot::Plot:0x007f043ce373e8 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043ce37230 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu1_1_8v}, :data=>"7aab582d-dc5f-49a3-8fda-380d706a1e9b"}, @xrange=[16819.166666666668, 16849.145833333332], @yrange=[1.78, 1.79]>], :options=>{:x_label=>"Time (days since epoch)", :y_label=>"CPU1 Voltage (W)", :zoom=>true, :width=>700, :xrange=>[16819.166666666668, 16849.145833333332], :yrange=>[1.78, 1.79]}}>], :data=>{"7aab582d-dc5f-49a3-8fda-380d706a1e9b"=>
#<Daru::DataFrame:69828083241940 @name = 7aab582d-dc5f-49a3-8fda-380d706a1e9b @size = 1399>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16819.1666 12.4040404 16.3535353       30.0       30.0 15.2626262       12.0       5.13        3.4 1.78969696       1.78 6115.15151 6135.75757 5781.81818     6120.0 6008.48484       92.0 
         1 16819.1875 12.7474226       17.0       30.0       30.0       16.0       12.0       5.13        3.4 1.78989690       1.78 6111.34020 6131.13402 5800.82474     6120.0 6012.37113 92.0412371 
         2 16819.2083 12.4000000 16.8700000       30.0       30.0 15.3400000       12.0       5.13        3.4     1.7899       1.78     6112.8     6140.4     5780.4     6120.0     6009.6       92.0 
         3 16819.2291 12.1648936 16.2872340       30.0       30.0       15.0       12.0       5.13        3.4 1.78978723       1.78 6116.17021 6187.65957 5777.87234     6120.0 6014.04255       92.0 
         4   16819.25 11.5412371       16.0       30.0       30.0       15.0       12.0       5.13        3.4       1.79       1.78 6110.10309 6199.17525 5779.79381     6120.0 6014.84536 92.0412371 
         5 16819.2708 11.1226415 15.2169811       30.0       30.0 14.0849056       12.0       5.13        3.4       1.79       1.78 6117.73584 6160.75471 5780.37735     6120.0 6015.84905 92.0377358 
         6 16819.2916 10.5445544 14.9603960       30.0       30.0 13.7227722       12.0       5.13        3.4       1.79       1.78 6118.81188 6144.95049 5779.00990     6120.0 6015.44554 92.0396039 
         7 16819.3125 10.4108910 14.6435643       30.0       30.0 13.1188118       12.0       5.13        3.4       1.79       1.78 6116.43564 6143.76237 5779.00990     6120.0 6011.88118 92.0792079 
         8 16819.3333 10.3602150 14.8279569       30.0       30.0 13.0215053       12.0       5.13        3.4       1.79       1.78 6116.12903 6131.61290 5781.93548     6120.0 6019.35483       92.0 
         9 16819.3541 10.3857142 14.7523809       30.0       30.0 13.1714285       12.0       5.13        3.4       1.79       1.78 6117.71428 6138.28571     5784.0     6120.0 6012.57142 92.0380952 
        10  16819.375 10.2722772 14.1089108       30.0       30.0       13.0       12.0       5.13        3.4       1.79       1.78 6115.24752 6130.69306 5786.13861     6120.0 6013.06930 92.1188118 
        11 16819.3958 9.85567010       14.0       30.0       30.0       13.0       12.0       5.13        3.4 1.78989690       1.78 6116.28865 6129.89690 5792.16494     6120.0 6013.60824 94.1030927 
        12 16819.4166 9.45192307       14.0       30.0       30.0 12.9230769       12.0       5.13        3.4       1.79       1.78 6115.38461 6133.84615 5786.53846     6120.0 6016.15384 93.8461538 
        13 16819.4375 9.47524752 13.9702970       30.0       30.0 12.3168316       12.0       5.13        3.4       1.79       1.78     6120.0 6127.12871 5775.44554     6120.0 6011.88118 92.0792079 
        14 16819.4583 9.80208333       14.0       30.0       30.0       13.0       12.0       5.13        3.4       1.79       1.78    6116.25     6137.5     5787.5     6120.0    6008.75 92.0833333 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...  

In [15]:
plot = Nyaplot::Plot.new
plot.add_with_df(filtered_df, :scatter, :cpu1_1_8v, :cpu1_temp)
plot.x_label("CPU1 Voltage (V)")
plot.y_label("CPU1 temperature (℃)")
plot.show

#<Nyaplot::Frame:0x007f043c60c3f8 @properties={:panes=>[#<Nyaplot::Plot:0x007f043c60ce98 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043c60cce0 @properties={:type=>:scatter, :options=>{:x=>:cpu1_1_8v, :y=>:cpu1_temp}, :data=>"92364cf0-f141-4a2c-bd66-8cae3dc204ec"}, @xrange=[1.78, 1.79], @yrange=[30.008928571428612, 53.68269230769232]>], :options=>{:x_label=>"CPU1 Voltage (V)", :y_label=>"CPU1 temperature (℃)", :zoom=>true, :width=>700, :xrange=>[1.78, 1.79], :yrange=>[30.008928571428612, 53.68269230769232]}}>], :data=>{"92364cf0-f141-4a2c-bd66-8cae3dc204ec"=>
#<Daru::DataFrame:69828086070360 @name = 92364cf0-f141-4a2c-bd66-8cae3dc204ec @size = 685>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
        43 16820.0625 15.3724489 19.9387755 30.0102040 30.0102040 18.5714285       12.0       5.13        3.4 1.78867346       1.78 6107.75510 6126.12244 5785.71428     6120.0 6002.44897 92.0816326 
        51 16820.2291 15.9950000 20.1500000 30.0100000 30.1100000       19.0       12.0       5.13        3.4      1.789       1.78     6109.2     6130.8     5775.6     6120.0     6008.4       92.0 
        52   16820.25       16.0 20.2666666 30.0285714 30.2190476       19.0       12.0       5.13        3.4 1.78866666       1.78 6113.14285 6126.85714 5774.85714     6120.0 6009.14285 92.0380952 
        53 16820.2708 15.9182692 20.5096153 30.0096153 30.2115384       19.0       12.0       5.13        3.4    1.78875       1.78 6107.30769 6124.61538 5777.30769     6120.0 6006.92307 92.0769230 
       378 16827.0416 15.7475247 19.8514851 30.0099009 30.2277227 18.7821782       12.0       5.13        3.4 1.78841584       1.78 6108.11881 6134.25742 5780.19801     6120.0 6005.94059 92.0396039 
       379 16827.0625 16.3490566 20.7358490 30.1132075 30.8490566 19.5188679       12.0       5.13        3.4 1.78764150       1.78 6103.01886 6131.32075 5782.64150     6120.0 6005.66037 92.0377358 
       380 16827.0833 16.9105263 21.1473684 30.3894736 31.4315789       20.0       12.0       5.13        3.4 1.78778947       1.78 6112.42105     6144.0 5775.15789     6120.0 6002.52631 92.1684210 
       381 16827.1041 17.4770642 21.9541284 31.1376146 31.8348623 20.7339449       12.0       5.13        3.4 1.78706422       1.78 6102.38532 6148.62385 5793.02752     6120.0 6007.70642 92.1100917 
       382  16827.125 17.8457943       22.0 31.5607476 32.1495327       21.0       12.0       5.13        3.4 1.78691588       1.78 6107.66355 6140.18691 5784.67289     6120.0 6004.48598 92.0373831 
       383 16827.1458       18.0 22.2395833 31.6354166 32.3854166       21.0       12.0       5.13        3.4 1.78572916       1.78    6108.75    6136.25     5797.5     6120.0    6001.25       92.0 
       384 16827.1666 18.0098039 22.0882352 31.4313725 32.3039215       21.0       12.0       5.13        3.4 1.78598039       1.78 6101.17647 6129.41176 5790.58823     6120.0 6002.35294 92.0392156 
       385 16827.1875       18.0 22.0761904 31.8761904 32.2952380       21.0       12.0       5.13        3.4 1.78561904       1.78 6109.71428 6133.71428 5793.14285     6120.0 6005.71428 92.0761904 
       386 16827.2083 18.0048076 22.4615384 32.1538461 32.4326923       21.0       12.0       5.13        3.4 1.78528846       1.78 6099.23076 6133.84615 5785.38461     6120.0 6002.30769 92.2692307 
       387 16827.2291 18.2252252 22.9369369 32.1531531 32.6756756       21.0       12.0       5.13        3.4 1.78513513       1.78 6105.94594 6131.89189 5785.94594     6120.0 6005.40540 92.1081081 
       388   16827.25 18.4565217       23.0 32.5652173 32.7173913 21.8152173       12.0       5.13        3.4 1.78434782       1.78 6109.56521 6127.82608 5774.34782     6120.0 6005.21739 92.0434782 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...

In [16]:
df2 = load_json("24h.json", "value")

#<Daru::DataFrame:69828089335060 @name = d23003ec-6c25-4787-a804-a10fec615621 @size = 3523>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         1 16848.6034       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         3 16848.6039       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         5 16848.6044       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         6 16848.6047       17.5       22.0       30.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         7 16848.6049       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6240.0     5760.0     6120.0     6000.0       92.0 
        12 16848.6062       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        13 16848.6065       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6240.0     5760.0     6120.0     6000.0       92.0 
        14 16848.6067       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
       ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...        ...

In [17]:

# 直近24時間のCPU温度・システムボード温度・環境温度の時間推移をプロット

plot = Nyaplot::Plot.new
plot.add_with_df(df2, :line, :time, :cpu1_temp).configure do |d|
  d.title("CPU1")
  d.color("#dd4444")
end
plot.add_with_df(df2, :line, :time, :cpu2_temp).configure do |d|
  d.title("CPU2")
  d.color("#ddaa44")
end
plot.add_with_df(df2, :line, :time, :systemboard_temp).configure do |d|
  d.title("Systemboard")
  d.color("#44bb44")
end
plot.add_with_df(df2, :line, :time, :ambient_temp).configure do |d|
  d.title("Ambient")
end
plot.x_label("Time (days since epoch)")
plot.y_label("Temperature (℃)")
plot.legend(true)
plot.show

#<Nyaplot::Frame:0x007f043f51f2a8 @properties={:panes=>[#<Nyaplot::Plot:0x007f043f519c68 @properties={:diagrams=>[#<Nyaplot::Diagram:0x007f043f519ab0 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu1_temp, :title=>"CPU1", :color=>"#dd4444"}, :data=>"d23003ec-6c25-4787-a804-a10fec615621"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[30.0, 71.0]>, #<Nyaplot::Diagram:0x007f043f519088 @properties={:type=>:line, :options=>{:x=>:time, :y=>:cpu2_temp, :title=>"CPU2", :color=>"#ddaa44"}, :data=>"d23003ec-6c25-4787-a804-a10fec615621"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[30.0, 66.0]>, #<Nyaplot::Diagram:0x007f043f5186b0 @properties={:type=>:line, :options=>{:x=>:time, :y=>:systemboard_temp, :title=>"Systemboard", :color=>"#44bb44"}, :data=>"d23003ec-6c25-4787-a804-a10fec615621"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[19.0, 33.0]>, #<Nyaplot::Diagram:0x007f043f51fc80 @properties={:type=>:line, :options=>{:x=>:time, :y=>:ambient_temp, :title=>"Ambient"}, :data=>"d23003ec-6c25-4787-a804-a10fec615621"}, @xrange=[16848.603182453702, 16849.602980578704], @yrange=[14.5, 27.5]>], :options=>{:x_label=>"Time (days since epoch)", :y_label=>"Temperature (℃)", :legend=>true, :zoom=>true, :width=>800, :xrange=>[16848.603182453702, 16849.602980578704], :yrange=>[14.5, 71.0]}}>], :data=>{"d23003ec-6c25-4787-a804-a10fec615621"=>
#<Daru::DataFrame:69828089335060 @name = d23003ec-6c25-4787-a804-a10fec615621 @size = 3523>
                 time ambient_te systemboar  cpu1_temp  cpu2_temp dimm_1a_te   main_12v    main_5v  main_3_3v  cpu1_1_8v  cpu2_1_8v   fan1_sys   fan2_sys   fan3_sys   fan4_sys   fan5_sys total_powe 
         0 16848.6031       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         1 16848.6034       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         2 16848.6037       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         3 16848.6039       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
         4 16848.6042       18.0       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         5 16848.6044       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         6 16848.6047       17.5       22.0       30.0       31.0       21.0       12.0       5.13        3.4       1.78       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         7 16848.6049       17.5       22.0       30.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
         8 16848.6052       17.5       22.0       31.0       31.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5880.0     6120.0     6000.0       92.0 
         9 16848.6054       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6000.0     6120.0     5760.0     6120.0     6000.0       92.0 
        10 16848.6057       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       1.78     6120.0     6120.0     5760.0     6120.0     6000.0       92.0 
        11 16848.6059       17.5       22.0       31.0       32.0       21.0       12.0       5.13        3.4       1.79       

In [19]:
if false
  plot = Nyaplot::Plot3D.new
  plot.add_with_df(df2, :particles, :total_power, :ambient_temp, :cpu1_temp).configure do |d|
    d.color("#44bb44")
  end
  plot.show
end